# Парсинг отзывов на телефоны с яндекс маркета.

## Нужно определить тональность данных заказчиком отзывов на телефоны, размеченного датасета для модели нет. Решение: взять отзывы с яндекс маркета, так как пользователь помимо текста ставит оценку по пятибальной шкале, которую можно трактовать как положительную или отрицательную.  Кроме того отзыв часто разделен на преимущества и недостатки товара, очевидно, что первая категория - это положительный текст, а вторая - негативный.

In [1]:
import requests
import bs4
import pandas as pd
import numpy as np
import re

## Выберем телефон, на каждой странице до 10 отзывов, будем поочередно переключаться по страницам, начиная с первой, и собирать отзывы.

In [ ]:
'''https://market.yandex.ru/product--smartfon-xiaomi-redmi-note-10s-nfc/914076054/reviews?nid=
54726&show-uid=16505936462756885604416001&track=srchlink&sku=101275506756&cpc=1i3NC4GInGEEwQbzVAb8WTIKMcvlNAD81X-
o_Ps81Stug7Xd6vaNVQ0KfydqaiELLkEq8BBMZ0SppDhdHFjebW0xISZCteoj3Ll-EvMXlTRi4F_v-_Ct2T8y5TyysLt62ur324wMLZuPAJ3asZC
in1dx9Wkw6_iU8GgwGcaR87bWIczj7cqc6g%2C%2C&do-waremd5=Zr-o8G4NI09iDq5RnH7GCg&page=2'''

In [2]:
url  = '''https://market.yandex.ru/product--smartfon-xiaomi-redmi-note-10s-nfc/914076054/reviews?nid=
54726&show-uid=16505936462756885604416001&track=srchlink&sku=101275506756&cpc=1i3NC4GInGEEwQbzVAb8WTIKMcvlNAD81X-
o_Ps81Stug7Xd6vaNVQ0KfydqaiELLkEq8BBMZ0SppDhdHFjebW0xISZCteoj3Ll-EvMXlTRi4F_v-_Ct2T8y5TyysLt62ur324wMLZuPAJ3asZC
in1dx9Wkw6_iU8GgwGcaR87bWIczj7cqc6g%2C%2C&do-waremd5=Zr-o8G4NI09iDq5RnH7GCg&page={}'''

In [3]:
req = requests.get(url.format(2))

In [4]:
req.text

'<!DOCTYPE html><!--BEGIN [@MarketNode/Root] / static--><html prefix="og: http://ogp.me/ns#" lang="ru" class="" data-zone-data="{&quot;page&quot;:&quot;market:product-reviews&quot;,&quot;service&quot;:&quot;market&quot;,&quot;subservice&quot;:&quot;market:product-reviews&quot;,&quot;ui&quot;:&quot;desktop&quot;,&quot;reqId&quot;:&quot;1651531753131/697e8e3da126f2bb670e7b330fde0500&quot;,&quot;userUid&quot;:&quot;3208415771651531753&quot;,&quot;regionId&quot;:213}" data-node-name="$page"><head><script nonce="Qgo7w0s7aPbJhdpBhx+JXA==" data-tid="da18e552">document.cookie = "js=1;path=/";</script><script nonce="Qgo7w0s7aPbJhdpBhx+JXA==" data-tid="da18e552">sessionStorage.setItem(\'__DEV_TOOLS_OPEN_KEY__\', \'false\')</script><script id="apiary-job-4ba" nonce="Qgo7w0s7aPbJhdpBhx+JXA==">document.cookie = "addressId=; Max-Age=-1; Domain=.market.yandex.ru; Path=/; Secure";document.cookie = "express_address=; Max-Age=-1; Domain=.market.yandex.ru; Path=/; Secure";document.cookie = "gps=; Max-Age

In [5]:
soup = bs4.BeautifulSoup(req.text, 'html.parser')

In [6]:
soup.prettify()

'<!DOCTYPE html>\n<!--BEGIN [@MarketNode/Root] / static-->\n<html class="" data-node-name="$page" data-zone-data=\'{"page":"market:product-reviews","service":"market","subservice":"market:product-reviews","ui":"desktop","reqId":"1651531753131/697e8e3da126f2bb670e7b330fde0500","userUid":"3208415771651531753","regionId":213}\' lang="ru" prefix="og: http://ogp.me/ns#">\n <head>\n  <script data-tid="da18e552" nonce="Qgo7w0s7aPbJhdpBhx+JXA==">\n   document.cookie = "js=1;path=/";\n  </script>\n  <script data-tid="da18e552" nonce="Qgo7w0s7aPbJhdpBhx+JXA==">\n   sessionStorage.setItem(\'__DEV_TOOLS_OPEN_KEY__\', \'false\')\n  </script>\n  <script id="apiary-job-4ba" nonce="Qgo7w0s7aPbJhdpBhx+JXA==">\n   document.cookie = "addressId=; Max-Age=-1; Domain=.market.yandex.ru; Path=/; Secure";document.cookie = "express_address=; Max-Age=-1; Domain=.market.yandex.ru; Path=/; Secure";document.cookie = "gps=; Max-Age=-1; Domain=.market.yandex.ru; Path=/; Secure";window["apiary-job-4ba"].parentNode.rem

## html выглядит отвратительно, проще распарсить сам текст.

In [7]:
soup.get_text()

'Стоит ли покупать Смартфон Xiaomi Redmi Note 10S NFC? Отзывы на Яндекс.Маркете. Страница 2{"widgets":{"@mobile/PopupManager":{"/popupManager":{"queue":[],"popups":{},"currentShownPopup":null,"previousShownPopup":null,"wasAnyPopupShown":false}}},"meta":{"/popupManager":{"name":"@mobile/PopupManager"}},"collections":{}}ЯндексМаркетКаталог{"widgets":{"@yandex-market/mandrel/LazyLoader-market":{"/header/catalogEntrypoint/catalog":{"widgetName":"@MarketNode/HeaderCatalog","widgetId":"HeaderCatalog","options":{"isSins":null},"cspNonce":"Qgo7w0s7aPbJhdpBhx+JXA==","placeholder":"TopMenuPanel","renderedOnce":false,"isLoaded":false,"isLoading":false,"error":false,"infinite":false}}},"meta":{"/header/catalogEntrypoint/catalog":{"name":"@yandex-market/mandrel/LazyLoader-market"}}}{"widgets":{"@MarketNode/HeaderCatalogEntrypoint":{"/header/catalogEntrypoint":{"widgetId":"HeaderCatalog","isActive":false,"isLoaded":false,"isSins":null,"simpleView":null,"isGrayCatalogButton":false}}},"meta":{"/header

## По ключевым словам вычленяем отзывы.

In [15]:
end = soup.get_text().find('Комментировать')
print(end)

310649


In [16]:
start = soup.get_text().find('Рейтинг: 5') + len('Рейтинг: 5')
print(start)

310221


In [17]:
soup.get_text()[start:end]

'Хороший товарТовар куплен на МаркетеОпыт использования: менее месяцаДостоинства: Экран, NFC, нет тормозов, быстрая зарядка, аккумулятор.Недостатки: Камера!!!Комментарий: Всем хорош, кроме камеры! Видео снимает хорошо, но фото убоги. В данном аппарате применён программный downgrade на камеру, снимает плохо из-за софта! Править софт не будут в угоду продаж более старших моделей с такой же аппаратной начинкой.Скрыть комментарии'

In [4]:
def find_reviews(req):
    soup = bs4.BeautifulSoup(req.text, 'html.parser')
    text = soup.get_text()
    start, end = 0, 0
    reviews = []
    while True:
        if text[end:].find('Рейтинг: 5') == -1: break
        start = end + text[end:].find('Рейтинг: 5')
        if text[start:].find('Комментировать') == -1: break
        end = start + text[start:].find('Комментировать')
        rev = text[start + len('Рейтинг: 5') : end]
        reviews.append(rev)
    return reviews     

In [19]:
print(*find_reviews(req), sep='\n\n')

Хороший товарТовар куплен на МаркетеОпыт использования: менее месяцаДостоинства: Экран, NFC, нет тормозов, быстрая зарядка, аккумулятор.Недостатки: Камера!!!Комментарий: Всем хорош, кроме камеры! Видео снимает хорошо, но фото убоги. В данном аппарате применён программный downgrade на камеру, снимает плохо из-за софта! Править софт не будут в угоду продаж более старших моделей с такой же аппаратной начинкой.Скрыть комментарии

Обычный товарТовар куплен на МаркетеОпыт использования: несколько месяцевДостоинства: Цена
Хорошо держит заряд при умеренном использованииНедостатки: ЛагаетКомментарий: Купил взамен Леново Вайб Шот. Через две недели использования очень разочаровался покупкой. Некорректно работает датчик отключения экрана при разговоре - открываются уведомления и кнопки верхней панели управления, делает снимки экрана, может во время разговора включить режим полета. Виснет при использовании блютуз. Камера посредственная, фотки плоские.
Не советую в покупкеСкрыть комментарии

Отличны

In [5]:
def save_reviews(reviews):
    with open('revs.txt', 'a') as f:
        for rev in reviews:
            f.write(rev + '\n')

## Для сборки отзывов выберем телефоны из разных ценовых категорий и с разным рейтингом.

In [226]:
# Взяты первые
# 600 отзывов
url1 = '''https://market.yandex.ru/product--smartfon-xiaomi-redmi-note-10s-nfc/914076054/reviews?nid=54726&show-
uid=16505936462756885604416001&track=srchlink&sku=101275506756&cpc=1i3NC4GInGEEwQbzVAb8WTIKMcvlNAD81X-
o_Ps81Stug7Xd6vaNVQ0KfydqaiELLkEq8BBMZ0SppDhdHFjebW0xISZCteoj3Ll-EvMXlTRi4F_v-_Ct2T8y5TyysLt62ur324wMLZuPAJ3asZC
in1dx9Wkw6_iU8GgwGcaR87bWIczj7cqc6g%2C%2C&do-waremd5=Zr-o8G4NI09iDq5RnH7GCg&page={}'''
# 20 отзывов
url2 = '''https://market.yandex.ru/product--telefon-maxvi-c20/14235913/reviews?sku=100707872355&do-waremd5=
30ATtmWa9ry-_B9LpbQSdg&cpc=oqTL_C1IHbQ3e7Sp4c7O1On-O_kP1CqlMm3Wltb8r3GCL0uCnJB4b5ZeUmxoIQXXPkcEmXIvEpfyI1xqjnJ
RmCsgEuBSXCnvSxRzGPsanJHYZF5MQ-LqZQw03KQPxr7SQNYDbyatMyH_Zju2cQ4x_swawzSMms6sPb17liBX6ppkmBqd2ySxHg%2C%2C&page={}'''
# 80 отзывов
url3 = '''https://market.yandex.ru/product--telefon-bq-1848-step/539573070/reviews?sku=100754161797&do-waremd5=l-
_mHagLzPt-9FjfR5xlVQ&cpc=EHBBe4OxIUKgafXR5EPLOnLAQJqsbLurHYVIdBAwAEMWU4JIhrhFobwJdgrI6icNA2eW-x0sGEg6ZLhuioV4fhA
YN3l7WN6VEsu9mklaixUktM7_lltvean_gkcH43F1CzFKPf1_dWZ-glGXvteK7ZMaAznAbLIlin_q9nutGj7lTH0ycHWqjg%2C%2C&page={}'''
# 30 отзывов
url4 = '''https://market.yandex.ru/product--smartfon-bq-5047l-like/820162682/reviews?sku=101169616459&do-
waremd5=U3Hve_DJfrMFm8jqwi_lCw&cpc=Rr-2WaBBbU_gUDnuOQR-s8SXuoxzNZc5dvG8a2_sZS0UhMR_Ft40vwVJ6dMWtZ8C6GacqhgE5J
CcmHWu7yoZpHjPxHTBYo_2K8hqxfK-mbxvAqWo_blkyL-xKk2C-vCP1yLPSjAGzPPhxqAypcqN766Ima3kBPecXITN1IAeKprSZi0HkxY6vA%2C
%2C&page={}'''
# 60 отзывов
url5 = '''https://market.yandex.ru/product--smartfon-samsung-galaxy-a03-core/1483515681/reviews?sku=101516211753
&do-waremd5=EAR-mUR5Guso40F6k1ez0A&cpc=ActhvfjtQcNWJjuWYR28xXfLVDVs0MIdt3OZ5Lp3v2-Ep_4oOR85Zb217hS2qNUop6QVayevW
MXr1mGbuOilKS_EjuG2Qy34pvo16Tfro7SSvAWAtuzK3yBt_Mfgs-q1dt5ZYIVTB3geTfS7QxZcUlBWVpPB9XhhzQmHen3xISJfwUn5FqEBXw%2C
%2C&page={}'''
# 500 отзывов
url6 = '''https://market.yandex.ru/product--smartfon-apple-iphone-12/722974019/reviews?sku=101077347753&do-waremd5
=owyo48QfIUYsuJxuSs9gLw&cpc=nW6mZIZqhXl_WGo_nBc2HI3-5rojj34rVpWzWOFlp9ShedCuixv-yOdBzsMw5NQuGzxXz6Fq1RIrbcP0lFD
AQU8DauLje4sZuYuGWL7x5Cy1edgGJdIbqGj6DHr9OT0fdA5j0O_hdY3-ZXH5L_161BscZMZGcBBXV-ioFJGHe9ka5Hljflf5KvUsa9TGew5q&
sort_by=rank&page={}'''
# 50 отзывов
url7 = '''https://market.yandex.ru/product--telefon-nokia-8000-4g/755201000/reviews?sku=101103363731&page={}'''
# 200 отзывов
url8 = '''https://market.yandex.ru/product--telefon-nokia-3310-dual-sim-2017/1725304280/reviews?g
lfilter=%2014871214%3A14896295_100326876850&sku=100326876850&cpa=&page={}'''
# 300 отзывов
url9 = '''https://market.yandex.ru/product--smartfon-xiaomi-redmi-6a/115757023/reviews?sku=100375026760&
do-waremd5=O9jI0jrmC7qlj1ebBL8XoA&cpc=_TXx5JiQ0uOATD8sqraUEhyDLfM2vAsKgZ3O3MpT7GlQQbfUXzKcN3s50jVBKS43QzE
sQABvF1CUZ78Inu9miBiL9YwTmwHD19NLhLd83YgMDxuBUJHSpsr2QZcWkq4gerSsZkRVlXDwfT5VxUcUoAiNeS2hl_mKt6ZcxOsY6Uun
W-NbAqZZKMXahIsbE4dcc93fpJuIZ8s%2C&page={}'''
# 160 отзывов
url10 = '''https://market.yandex.ru/product--smartfon-lenovo-p780-8gb/10546687/reviews?sku=101276984776&d
o-waremd5=uc8CRHX6cQKxVOnYW3BVjQ&cpc=W-l0D6DMb0w4iqGDkFgHNJM8usnHSLibS68d83d8EoJ9rtxux9YlPT-WMJ6irnUWgtrzD-W
SszJ2C3jTHDo2Oc4ILv4jpl1RPddoEgWTVKAVYZAIox915b0Pbn7q7Le_yWHHvAD8Usl-xDiOcW-L9I4yNwCRMUrkrbILrbe7pgWKGS9r1uO
a3eIHEgInVHs_&page={}'''

## Соберем 2000 отзывов, сохраняя их в файл. Капча яндекс маркета обходится сменой ip.

In [225]:
# req = requests.get(url1.format(60))
# print(req.status_code)
# rev = find_reviews(req)
# for i, text in enumerate(rev):
#     rev[i] = text.replace('\n', '')
# print(*rev, sep='\n\n')
# save_reviews(rev)

200
Отличный товарОпыт использования: менее месяцаДостоинства: Пользуюсь третий день, пока нареканий нет, всё нравится.В дальнейшем покажет время.Недостатки: Нет

Отличный товарОпыт использования: несколько месяцевДостоинства: Впринципе очень хороший телефонНедостатки: Звук чуть чуть тихий, но качественный!Комментарий: Рекомендую за свою цену

Отличный товарТовар куплен на МаркетеОпыт использования: менее месяцаДостоинства: Очень практичный

Отличный товарТовар куплен на МаркетеОпыт использования: менее месяцаДостоинства: Шустрый

Отличный товарТовар куплен на МаркетеОпыт использования: менее месяцаХороший телефон

Отличный товарОпыт использования: менее месяцаДостоинства: ЦенаНедостатки: Нету покаКомментарий: Пока ещё нету

Отличный товарОпыт использования: несколько месяцевДостоинства: Внешний вид смартфона, долгая работа аккумулятора, очень насыщенный дисплей и ценаНедостатки: Нет такого

Отличный товарОпыт использования: менее месяцаДостоинства: Картинка совпадает с фактомНедостатк

## Возьмем все отзывы с файла, детально изучим.

In [227]:
with open('revs.txt', 'r') as f:
    data = [line.strip() for line in f.readlines()]
print(*data, sep='\n\n')    

Отличный товарТовар куплен на МаркетеУвеличитьОпыт использования: менее месяцаДостоинства: Наклеена защитная пленка,чехол из коробки ,довольно емкая батарея, отдельный слот для карты памяти и двух симок . Качество съемки и быстродействие можно сказать отличное. Соотношение цена-качествоНедостатки: Предустановленные приложения производителя которые и не нужны но и удалить их нельзяКомментарий: Полностью соответствует моим потребностям!Особенно порадовала батарея ,подзаряжать в течении дня не пришлось не смотря на то пользовался навигатором 6-7 часов и постоянно был включен мобильный интернет. Посмотрим на сколько она деградирует за годЕщё 55 комментариев

Отличный товарТовар куплен на МаркетеОпыт использования: менее месяцаДостоинства: 1. Хороший дизайн2. Камера довольно высокого уровня и есть несколько дополнительных функций для съёмки видео (замедление и ускорение).3. Вариант с 6 гигами оперативы делает его довольно шустрым смартфоном.4. Фронтальная камера внутри экрана, а не монобров

In [228]:
print('Всего отзывов - ', len(data), '\n', 'Уникальных отзывов - ', len(set(data)), sep='')

Всего отзывов - 2000
Уникальных отзывов - 1921


## Разложим каждый отзыв на Достоинства и Недостатки как на яндекс маркете, получим уже размеченные данные для обучения модели. Комментарий тоже сохраним для дополнительной информации, отзывов и так мало. Еще сохраним итоговую оценку товара по пятибальной шкале яндекс маркета.  

In [229]:
def find(string, temp):
    res = string.find(temp)
    if res != -1: return res
    else: return None

def decompose(review):
    result = []
    review = re.sub(r'Скрыть комментарии\Z', '', review)
    review = re.sub(r'Ещё [0-9]+ коммен.*\Z', '', review)       
    if find(review, 'Достоинства: '):
        if find(review, 'Недостатки:'):
            result.append(review[find(review, 'Достоинства: ') + len('Достоинства: ') : find(review, 'Недостатки:')])
        else:
            result.append(review[find(review, 'Достоинства: ') + len('Достоинства: ') : find(review, 'Комментарий:')])
    else:
        result.append(None)
    if find(review, 'Недостатки:'):
        result.append(review[find(review, 'Недостатки: ') + len('Недостатки: ') : find(review, 'Комментарий:')])
    else:
        result.append(None)    
    if find(review, 'Комментарий:'):
        result.append(review[find(review, 'Комментарий: ') + len('Комментарий: ') : ])
    else:
        result.append(None)     
    result.append(review.split()[0])
    return result

In [230]:
parsed_data = list(map(decompose, data))
print(*parsed_data[0], sep='\n\n')

Наклеена защитная пленка,чехол из коробки ,довольно емкая батарея, отдельный слот для карты памяти и двух симок . Качество съемки и быстродействие можно сказать отличное. Соотношение цена-качество

Предустановленные приложения производителя которые и не нужны но и удалить их нельзя

Полностью соответствует моим потребностям!Особенно порадовала батарея ,подзаряжать в течении дня не пришлось не смотря на то пользовался навигатором 6-7 часов и постоянно был включен мобильный интернет. Посмотрим на сколько она деградирует за год

Отличный


## Некоторые отзывы не разделены на достоинства и недостатки, сохраним весь их текст как комментарий.

In [231]:
old_reviews = []
for i, el in enumerate(parsed_data):
    if el[0]==el[1]==el[2] and el[0] is None:
        old_reviews.append(i)
print(len(old_reviews), 'отзыв без деления на достоинства и недостатки', '\n\nПример:', data[old_reviews[0]])        

112 отзыв без деления на достоинства и недостатки 

Пример: Отличный товарТовар куплен на МаркетеКуплен в 07.2021 за 18к. В использовании у человека с потребностями "навигатор", "wa", "viber". Пользователь в восторгеСкрыть комментарии


Удалим все кроме текста отзыва и занесем этот текст как комментарий

In [232]:
def delete_meta(review):
    review = re.sub(r'\A\S+й товар', '', review) 
    review = re.sub(r'\AТовар куплен на Маркете', '', review) 
    review = re.sub(r'\AУвеличить', '', review) 
    review = re.sub(r'\AОпыт использования: \w+ (года|год|лет|месяца|месяцев|месяц)', '', review) 
    review = re.sub(r'Скрыть комментарии\Z', '', review)
    review = re.sub(r'Ещё [0-9]+ коммен.*\Z', '', review)    
    return review

In [233]:
for i in old_reviews:
    parsed_data[i][2] = delete_meta(data[i])

## Создадим датафрейм из получившихся отзывов, посмотрим на результат.

In [234]:
df = pd.DataFrame(parsed_data, columns=['pos', 'neg', 'komment', 'result'])

In [235]:
df[200:220]

pos  \
200                                  Хорошая звонилка.   
201                            Долго держит зарядку...   
202                                                Нет   
203                                            Никаких   
204                                                  -   
205                                 Слышимость хорошая   
206                                               None   
207              Бабушке старой пойдет громкий динамик   
208                                               None   
209                        Цена соответствует качеству   
210                                   Обычная звонилка   
211                     Маленький, громкий звук кнопок   
212                                 Цена, очень лёгкий   
213  Принимает звонки и смс, и отправляет. Есть рад...   
214                     Копия НОКИА 105. Звук хороший.   
215  телефон хороший но просто нельзя было скачать ...   
216                                               None   
217  Неплохой функционал за можно сказать даром. Ау...   
218  всё отлично. качество микрофона и главное гром...   
219                                             Дизайн   

                                                   neg  \
200  Но не надолго, через полгода ежедневного испол...   
201                               За эту цену не нашел   
202                                  Даже не включился   
203  Пришел без зарядного устройства! При зего заря...   
204  Товар пришел в нерабочем состоянии, оформил во...   
205                                        Нет зарядки   
206                                               None   
207                                               None   
208                           Нет зарядного устройства   
209            Просите оценить камеру, а её там нет)))   
210                                               None   
211  минимум настроек, в поставке нет ни зарядки ни...   
212                                      Все остальное   
213  1) Сам выключается, когда посчитает нужным: пр...   
214  В телефоне нет БЫСТРОГО НАБОРА, нельзя добавит...   
215  когда ты его включаеш то ети кнопки очень громкие   
216                                               None   
217  Парень в техподдержке как партизан на допросе,...   
218  в наушниках работает только один канал, батаре...   
219  Качество звука динамика-как в стакане через ст...   

                                               komment    result  
200                                               None   Хороший  
201                                               None  Отличный  
202  Телефон пришёл, естественно, без зарядного уст...   Ужасный  
203                                               None   Ужасный  
204  Телефон работал только при подключении к розетке.   Ужасный  
205                                               None  Отличный  
206  Телефончик новый, упакован хорошо, все целое. ...  Отличный  
207                                               None  Отличный  
208                                               None   Хороший  
209  Заказывала красный, а пришёл голубой. Но это н...  Отличный  
210          Заказывала синий цвет, а прислали красный    Плохой  
211                                               None   Обычный  
212  Покупал в интернет магазине за 200руб. Пришел ...    Плохой  
213  Радио ловится приемлемо, и не только на наушни...    Плохой  
214          Впечатление неважное. Пожалел, что купил.    Плохой  
215                                               None   Хороший  
216                                  Своих денег стоит  Отличный  
217  Если бы была возможность(возможно это невозмож...   Хороший  
218  модель для тех кому от телефона нужны в основн...  Отличный  
219  Всем кто ищет бюджетный телефон с хорошим каче...    Плохой

## Все соответствует здравому смыслу, сохраним датасет в файл.

In [236]:
df.to_csv('revs.csv', index=False)

# Обучение модели в следующем ноутбуке.